In [5]:
from utils.BackTest import Engine, Strategy
import pandas as pd

In [6]:
df = pd.read_csv("../data/processed/features_trading_strategy.csv")

In [7]:
df = df.rename(columns={'OPEN':'Open','HIGH':'High','LOW':'Low','CLOSE':'Close','VOLUME':'Volume'})

In [8]:
df['Close']

0       51509.99
1       51995.58
2       51656.96
3       51456.01
4       51288.42
          ...   
8995    89278.88
8996    90035.37
8997    90154.00
8998    90300.01
8999    87132.80
Name: Close, Length: 9000, dtype: float64

In [ ]:
class SMACrossOver(Strategy):
    def __init__(self):
        super().__init__()
        # Default multipliers for TP and SL calculations
        self.tp_atr_multiplier = 1.5   
        self.sl_atr_multiplier = 1.5  
    def on_bar(self):
        # Get current bar data
        current_bar = self.data.loc[self.current_idx]
        close = current_bar['Close']
        sma20 = current_bar['SMA20']
        sma50 = current_bar['SMA50']

        # For multiple positions, get all BTC positions
        btc_positions = [p for p in self.positions if p.ticker == 'BTC']

        # Buy signal: SMA20 > SMA50, and we allow up to 5 positions.
        if sma20 > sma50:
            if len(btc_positions) < 5:
                # Use 10% of available cash to determine the order size.
                order_size = 0.1 * self.cash / close
                self.buy('BTC', order_size)
                print(f"{self.current_idx} BUY signal: entering new position, order size {order_size:.4f}")
            else:
                print(f"{self.current_idx} BUY signal: maximum BTC positions reached.")


In [10]:
df['SMA50'] = df['Close'].rolling(window=50).mean()

In [11]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9000 entries, 0 to 8999
Data columns (total 47 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   datetime            9000 non-null   object 
 1   Open                9000 non-null   float64
 2   High                9000 non-null   float64
 3   Low                 9000 non-null   float64
 4   Close               9000 non-null   float64
 5   TOTAL_TRADES        9000 non-null   int64  
 6   TOTAL_TRADES_BUY    9000 non-null   int64  
 7   TOTAL_TRADES_SELL   9000 non-null   int64  
 8   Volume              9000 non-null   float64
 9   VOLUME_BUY          9000 non-null   float64
 10  VOLUME_SELL         9000 non-null   float64
 11  return              8999 non-null   float64
 12  log_return          8999 non-null   float64
 13  hourly_volatility   8988 non-null   float64
 14  EMA_8               9000 non-null   float64
 15  EMA_13              9000 non-null   float64
 16  EMA_21

In [12]:
df['datetime'] = pd.to_datetime(df['datetime'])
df = df.set_index('datetime')

In [13]:
df_filtered = df.dropna()
df_filtered

Open      High       Low     Close  \
datetime                                                            
2024-03-02 02:00:00+00:00  62030.01  62216.71  61949.03  62111.18   
2024-03-02 03:00:00+00:00  62111.18  62426.70  62025.00  62307.45   
2024-03-02 04:00:00+00:00  62307.45  62307.45  62035.95  62035.95   
2024-03-02 05:00:00+00:00  62035.95  62079.99  61752.30  62006.55   
2024-03-02 06:00:00+00:00  62006.55  62256.00  61930.00  61946.00   
...                             ...       ...       ...       ...   
2025-03-03 14:00:00+00:00  93586.83  93721.37  89136.45  89278.88   
2025-03-03 15:00:00+00:00  89278.88  91307.00  89117.00  90035.37   
2025-03-03 16:00:00+00:00  90035.37  90750.91  89691.02  90154.00   
2025-03-03 17:00:00+00:00  90154.00  91000.00  89912.00  90300.01   
2025-03-03 18:00:00+00:00  90300.01  90450.47  86781.98  87132.80   

                           TOTAL_TRADES  TOTAL_TRADES_BUY  TOTAL_TRADES_SELL  \
datetime                                                                       
2024-03-02 02:00:00+00:00         56088             24390              31698   
2024-03-02 03:00:00+00:00         67185             27772              39413   
2024-03-02 04:00:00+00:00         56098             24794              31304   
2024-03-02 05:00:00+00:00         65329             23953              41376   
2024-03-02 06:00:00+00:00         57826             25109              32717   
...                                 ...               ...                ...   
2025-03-03 14:00:00+00:00        909864            449798             460066   
2025-03-03 15:00:00+00:00        815439            415993             399446   
2025-03-03 16:00:00+00:00        448660            224630             224030   
2025-03-03 17:00:00+00:00        331538            185179             146359   
2025-03-03 18:00:00+00:00        868682            423108             445574   

                               Volume  VOLUME_BUY  VOLUME_SELL  ...  \
datetime                                                        ...   
2024-03-02 02:00:00+00:00  1153.46042   607.80296    545.65746  ...   
2024-03-02 03:00:00+00:00  1465.47878   802.61870    662.86008  ...   
2024-03-02 04:00:00+00:00  1147.71004   516.23228    631.47776  ...   
2024-03-02 05:00:00+00:00  1415.65823   637.30577    778.35246  ...   
2024-03-02 06:00:00+00:00  1059.53378   543.92419    515.60959  ...   
...                               ...         ...          ...  ...   
2025-03-03 14:00:00+00:00  6172.59027  2600.65274   3571.93753  ...   
2025-03-03 15:00:00+00:00  5771.66863  2921.20810   2850.46053  ...   
2025-03-03 16:00:00+00:00  2111.23659  1038.58417   1072.65242  ...   
2025-03-03 17:00:00+00:00  1626.75033   767.44993    859.30040  ...   
2025-03-03 18:00:00+00:00  7319.60685  3223.13282   4096.47403  ...   

                                  OBV   OBV_EMA20  OBV_Signal      H-L  \
datetime                                                                 
2024-03-02 02:00:00+00:00  1153.46042 -263.362181           1   267.68   
2024-03-02 03:00:00+00:00  1465.47878  -98.710661           0   401.70   
2024-03-02 04:00:00+00:00 -1147.71004 -198.615364          -1   271.50   
2024-03-02 05:00:00+00:00 -1415.65823 -314.524208           0   327.69   
2024-03-02 06:00:00+00:00 -1059.53378 -385.477501           0   326.00   
...                               ...         ...         ...      ...   
2025-03-03 14:00:00+00:00 -6172.59027   91.667872          -1  4584.92   
2025-03-03 15:00:00+00:00  5771.66863  632.620325           1  2190.00   
2025-03-03 16:00:00+00:00  2111.23659  773.440922           0  1059.89   
2025-03-03 17:00:00+00:00  1626.75033  854.708485           0  1088.00   
2025-03-03 18:00:00+00:00 -7319.60685   76.202262          -1  3668.49   

                              H-PC     L-PC       TR          ATR  ATR_Signal  \
datetime                                                                        
2024-03-02 02:00:00+00:00   186.70    80.98

In [ ]:
e = Engine()
e.add_data(df_filtered)
e.add_strategy(SMACrossOver())
stats = e.run()     

  2%|▏         | 214/8801 [00:00<00:07, 1080.53it/s]

2024-03-02 02:00:00+00:00 BUY signal: entering new position, order size 0.1610
Index: 2024-03-02 02:00:00+00:00 | Cash: 100000.00 | Total position value: 0.00 | Total value: 100000.00
2024-03-02 03:00:00+00:00 New position opened: <Position: BTC size: 0.1610016103381066 entry: 62111.18>
2024-03-02 03:00:00+00:00 BUY signal: entering new position, order size 0.1605
Index: 2024-03-02 03:00:00+00:00 | Cash: 90000.00 | Total position value: 10031.60 | Total value: 100031.60
2024-03-02 04:00:00+00:00 Take Profit Not Filled. Limit: 65216.739 / High: 62307.45
2024-03-02 04:00:00+00:00 Stop Loss Not Filled. Limit: 59005.621 / Low: 62035.95
2024-03-02 04:00:00+00:00 New position opened: <Position: BTC size: 0.16049445130558224 entry: 62307.45>
2024-03-02 04:00:00+00:00 BUY signal: entering new position, order size 0.1612
Index: 2024-03-02 04:00:00+00:00 | Cash: 80000.00 | Total position value: 19944.31 | Total value: 99944.31
2024-03-02 05:00:00+00:00 Take Profit Not Filled. Limit: 65216.739 / 

  6%|▋         | 558/8801 [00:00<00:05, 1559.40it/s]

2024-03-11 06:00:00+00:00 Take Profit Not Filled. Limit: 71201.13 / High: 69371.81
2024-03-11 06:00:00+00:00 Stop Loss Not Filled. Limit: 64420.07 / Low: 68445.91
2024-03-11 06:00:00+00:00 Take Profit Not Filled. Limit: 71757.0105 / High: 69371.81
2024-03-11 06:00:00+00:00 Stop Loss Not Filled. Limit: 64923.00949999999 / Low: 68445.91
2024-03-11 06:00:00+00:00 Take Profit Not Filled. Limit: 72006.9105 / High: 69371.81
2024-03-11 06:00:00+00:00 Stop Loss Not Filled. Limit: 65149.10949999999 / Low: 68445.91
2024-03-11 06:00:00+00:00 Take Profit Not Filled. Limit: 72307.18950000001 / High: 69371.81
2024-03-11 06:00:00+00:00 Stop Loss Not Filled. Limit: 65420.7905 / Low: 68445.91
2024-03-11 06:00:00+00:00 BUY signal: maximum BTC positions reached.
Index: 2024-03-11 06:00:00+00:00 | Cash: 56500.00 | Total position value: 50792.02 | Total value: 107292.02
2024-03-11 07:00:00+00:00 Take Profit Filled. Limit: 70998.48000000001 / High: 71298.0
2024-03-11 07:00:00+00:00 Position closed for ticke

  8%|▊         | 715/8801 [00:00<00:06, 1276.33it/s]

...

2025-02-08 21:00:00+00:00 Take Profit Not Filled. Limit: 102575.76 / High: 96600.0
2025-02-08 21:00:00+00:00 Stop Loss Not Filled. Limit: 92806.64 / Low: 96360.0
2025-02-08 21:00:00+00:00 Take Profit Not Filled. Limit: 101807.98950000001 / High: 96600.0
2025-02-08 21:00:00+00:00 Stop Loss Not Filled. Limit: 92111.9905 / Low: 96360.0
Index: 2025-02-08 21:00:00+00:00 | Cash: 64500.00 | Total position value: 48839.64 | Total value: 113339.64
2025-02-08 22:00:00+00:00 Take Profit Not Filled. Limit: 105661.185 / High: 96712.0
2025-02-08 22:00:00+00:00 Stop Loss Not Filled. Limit: 95598.215 / Low: 96388.88
2025-02-08 22:00:00+00:00 Take Profit Not Filled. Limit: 105055.776 / High: 96712.0
2025-02-08 22:00:00+00:00 Stop Loss Not Filled. Limit: 95050.46399999999 / Low: 96388.88
2025-02-08 22:00:00+00:00 Take Profit Not Filled. Limit: 103809.28950000001 / High: 96712.0
2025-02-08 22:00:00+00:00 Stop Loss Not Filled. Limit: 93922.6905 / Low: 96388.88
2025-02-08 22:00:00+00:00 Take Profit Not Fil

 97%|█████████▋| 8567/8801 [00:08<00:00, 910.29it/s]

2025-02-16 06:00:00+00:00 Take Profit Not Filled. Limit: 100623.22200000001 / High: 97625.63
2025-02-16 06:00:00+00:00 Stop Loss Not Filled. Limit: 91040.05799999999 / Low: 97451.99
2025-02-16 06:00:00+00:00 BUY signal: maximum BTC positions reached.
Index: 2025-02-16 06:00:00+00:00 | Cash: 63500.00 | Total position value: 50309.89 | Total value: 113809.89
2025-02-16 07:00:00+00:00 Take Profit Not Filled. Limit: 103809.28950000001 / High: 97487.27
2025-02-16 07:00:00+00:00 Stop Loss Not Filled. Limit: 93922.6905 / Low: 97212.0
2025-02-16 07:00:00+00:00 Take Profit Not Filled. Limit: 102575.76 / High: 97487.27
2025-02-16 07:00:00+00:00 Stop Loss Not Filled. Limit: 92806.64 / Low: 97212.0
2025-02-16 07:00:00+00:00 Take Profit Not Filled. Limit: 101807.98950000001 / High: 97487.27
2025-02-16 07:00:00+00:00 Stop Loss Not Filled. Limit: 92111.9905 / Low: 97212.0
2025-02-16 07:00:00+00:00 Take Profit Not Filled. Limit: 99932.469 / High: 97487.27
2025-02-16 07:00:00+00:00 Stop Loss Not Filled

100%|██████████| 8801/8801 [00:08<00:00, 1026.03it/s]

2025-02-25 07:00:00+00:00 Take Profit Not Filled. Limit: 99932.469 / High: 91441.82
2025-02-25 07:00:00+00:00 Stop Loss Filled. Limit: 90415.091 / Low: 88200.0
2025-02-25 07:00:00+00:00 Position closed for ticker BTC at 90415.091
Index: 2025-02-25 07:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 08:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 09:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 10:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 11:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 12:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 13:00:00+00:00 | Cash: 110500.00 | Total position value: 0.00 | Total value: 110500.00
Index: 2025-02-25 14:00:00+00:00 | 

In [15]:
e.plot()